# Obtain

In [1]:
## Import necessary libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import datetime as dt

In [2]:
## Set options for displaying Pandas DataFrames
pd.options.display.max_columns = 100
pd.options.display.max_rows = 120

In [5]:
cols = list(voter_elecs.columns)
mixed_col_idx = [3,4,5,6,8,27,29,30,33,37]
for col in mixed_col_idx:
    print(cols[col])

election_lbl
voting_method
voted_party_cd
pct_label
vtd_label
precinct_abbrv
super_court_abbrv
judic_dist_abbrv
school_dist_abbrv
vtd_abbrv


In [6]:
## Load in NC statewide voter history and info by election

# Set dtypes for mixed columns
dtypes={'election_lbl': str,
        'voting_method': str, 
        'voted_party_cd': str,
        'pct_label': str,
        'vtd_label': str,
        'precinct_abbrv': str, 
        'super_court_abbrv': str,
        'judic_dist_abbrv': str,
        'school_dist_abbrv': str,
        'vtd_abbrv': str
       }
# Parse dates for datetime variables
parse_dates = ['election_lbl']

# Read in df
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs.gz',
                          dtype=dtypes, parse_dates=parse_dates)
voter_elecs.head()

ncid       election_desc  voter_reg_num election_lbl     voting_method  \
0  AA100000  11/03/2020 GENERAL      9050398.0   2020-11-03  ABSENTEE ONESTOP   
1  AA100000  11/06/2018 GENERAL            NaN          NaT               NaN   
2  AA100000  11/08/2016 GENERAL      9050398.0   2016-11-08  ABSENTEE ONESTOP   
3  AA100000  11/04/2014 GENERAL            NaN          NaT               NaN   
4  AA100000  11/06/2012 GENERAL            NaN          NaT               NaN   

  voted_party_cd pct_label  voted_county_id vtd_label  county_id  \
0            UNA        07              1.0        07          1   
1            NaN       NaN              NaN       NaN          1   
2            UNA        07              1.0        07          1   
3            NaN       NaN              NaN       NaN          1   
4            NaN       NaN              NaN       NaN          1   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED  BOYDSTUN      JAMES      ARCHIE   
1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES      ARCHIE   
2            ACTIVE                 VERIFIED  BOYDSTUN      JAMES      ARCHIE   
3            ACTIVE                 VERIFIED  BOYDSTUN      JAMES      ARCHIE   
4            ACTIVE                 VERIFIED  BOYDSTUN      JAMES      ARCHIE   

     res_street_address res_city_desc state_cd  zip_code race_code  \
0  3318  NESTER'S CT           GRAHAM       NC   27253.0         W   
1  3318  NESTER'S CT           GRAHAM       NC   27253.0         W   
2  3318  NESTER'S CT           GRAHAM       NC   27253.0         W   
3  3318  NESTER'S CT           GRAHAM       NC   27253.0         W   
4  3318  NESTER'S CT           GRAHAM       NC   27253.0         W   

  ethnic_code party_cd gender_code  birth_age birth_state drivers_lic  \
0          NL      UNA           M         54          OK           N   
1          NL      UNA           M         54          OK           N   
2          NL      UNA           M         54          OK           N   
3          NL      UNA           M         54          OK           N   
4          NL      UNA           M         54          OK           N   

   registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0  06/21/1996             07             13.0               15A   
1  06/21/1996             07             13.0               15A   
2  06/21/1996             07             13.0               15A   
3  06/21/1996             07             13.0               15A   
4  06/21/1996             07             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv  
0          17.0                N        1967        07  
1          17.0                N        1967        07  
2          17.0                N        1967        07  
3          17.0                N        1967        07  
4          17.0                N        1967        07

# Scrub and Explore

In [7]:
## Check metadata for df
voter_elecs.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 44346931 entries, 0 to 44346930
Data columns (total 38 columns):
ncid                        44346931 non-null object
election_desc               44346931 non-null object
voter_reg_num               20241696 non-null float64
election_lbl                20241696 non-null datetime64[ns]
voting_method               20241696 non-null object
voted_party_cd              20233459 non-null object
pct_label                   20241696 non-null object
voted_county_id             20241696 non-null float64
vtd_label                   19731247 non-null object
county_id                   44346931 non-null int64
voter_status_desc           44346931 non-null object
voter_status_reason_desc    44346925 non-null object
last_name                   44345911 non-null object
first_name                  44346241 non-null object
middle_name                 41226390 non-null object
res_street_address          44346931 non-null object
res_city_desc               

## Drop Duplicate Records

In [8]:
## Check for duplicate entries
voter_elecs.duplicated().sum()

0

In [6]:
## Inspect duplicate entries in voter history data
# voter_elecs.loc[voter_elecs.duplicated()]

In [7]:
## Remove duplicate entries from records of voter history
# voter_elecs.drop_duplicates(inplace=True)

In [9]:
## Check length of new df
len(voter_elecs)

44346931

In [10]:
## Check the intended length of the new df if every unique ncid
  ## appears only once for each election description
voter_elecs['ncid'].nunique() * voter_elecs['election_desc'].nunique()

44346540

In [11]:
44346931 - 44346540

391

In [12]:
## There are 391 instances where an ncid shows up as casting a vote
  ## more than once in the same election
voter_elecs.duplicated(subset=['ncid', 'election_desc']).sum()

391

In [13]:
## A total of 310 individuals show up more than once for a single election
dup_ncid_elecs = voter_elecs.loc[voter_elecs.duplicated(subset=['ncid', 'election_desc'], keep=False)]
display(dup_ncid_elecs.head())
dup_ncid_elecs['ncid'].nunique()

ncid       election_desc  voter_reg_num election_lbl  \
210164   AA16823  11/08/2016 GENERAL      2332350.0   2016-11-08   
210165   AA16823  11/08/2016 GENERAL      2332350.0   2016-11-08   
232835  AA174391  11/06/2012 GENERAL     10191737.0   2012-11-06   
232836  AA174391  11/06/2012 GENERAL     10191737.0   2012-11-06   
566394   AB14598  11/06/2012 GENERAL        32922.0   2012-11-06   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
210164         IN-PERSON            REP        02              1.0        02   
210165  ABSENTEE ONESTOP            DEM        LI             68.0        LI   
232835         IN-PERSON            DEM       064              1.0       064   
232836  ABSENTEE ONESTOP            DEM       146             60.0       146   
566394         IN-PERSON            REP        B2              2.0        B2   

        county_id voter_status_desc voter_status_reason_desc last_name  \
210164          1            ACTIVE                 VERIFIED     GANTT   
210165          1            ACTIVE                 VERIFIED     GANTT   
232835         41            ACTIVE                 VERIFIED    WARREN   
232836         41            ACTIVE                 VERIFIED    WARREN   
566394          4            ACTIVE                 VERIFIED     SMITH   

       first_name middle_name  res_street_address res_city_desc state_cd  \
210164       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210165       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
232835     LATOYA      DIONNE   4388  KELSO DR       HIGH POINT       NC   
232836     LATOYA      DIONNE   4388  KELSO DR       HIGH POINT       NC   
566394    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
210164   27215.0         U          UN      REP           M         78   
210165   27215.0         U          UN      REP           M         78   
232835   27265.0         B          NL      DEM           F         42   
232836   27265.0         B          NL      DEM           F         42   
566394   28091.0         B          UN      DEM           M         49   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
210164          OR           N  09/29/1973             02             13.0   
210165          OR           N  09/29/1973             02             13.0   
232835          NC           Y  10/14/2016            H25              6.0   
232836          NC           Y  10/14/2016            H25              6.0   
566394          NC           Y  11/02/2012           LILE              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
210164               15A              15A             24.0            64.0   
210165               15A              15A             24.0            64.0   
232835               18B               18             27.0            62.0   
232836               18B               18             27.0            62.0   
566394               16A              16A             25.0            55.0   

       school_dist_abbrv  dist_1_abbrv confidential_ind  birth_year vtd_abbrv  
210164               NaN          17.0                N        1943        02  
210165               NaN          17.0                N        1943        02  
232835               006          24.0                N        1979       H25  
232836               006          24.0                N        1979       H25  
566394              SCH2          21.0                N        1972      LILE

310

In [14]:
## Examine the complete recent voting history of the 310 ncid's that show up 
  ## multiple times for a single election to investigate how the records differ
    ## and determine which record(s) to drop
for ncid in dup_ncid_elecs['ncid'].unique():
    display(voter_elecs.loc[voter_elecs['ncid']==ncid])

ncid       election_desc  voter_reg_num election_lbl  \
210162  AA16823  11/03/2020 GENERAL      2332350.0   2020-11-03   
210163  AA16823  11/06/2018 GENERAL      2332350.0   2018-11-06   
210164  AA16823  11/08/2016 GENERAL      2332350.0   2016-11-08   
210165  AA16823  11/08/2016 GENERAL      2332350.0   2016-11-08   
210166  AA16823  11/04/2014 GENERAL      2332350.0   2014-11-04   
210167  AA16823  11/06/2012 GENERAL      2332350.0   2012-11-06   
210168  AA16823                None            NaN          NaT   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
210162         IN-PERSON            REP        02              1.0        02   
210163         IN-PERSON            REP        02              1.0        02   
210164         IN-PERSON            REP        02              1.0        02   
210165  ABSENTEE ONESTOP            DEM        LI             68.0        LI   
210166         IN-PERSON            REP        02              1.0        02   
210167  ABSENTEE ONESTOP            REP        02              1.0        02   
210168               NaN            NaN       NaN              NaN       NaN   

        county_id voter_status_desc voter_status_reason_desc last_name  \
210162          1            ACTIVE                 VERIFIED     GANTT   
210163          1            ACTIVE                 VERIFIED     GANTT   
210164          1            ACTIVE                 VERIFIED     GANTT   
210165          1            ACTIVE                 VERIFIED     GANTT   
210166          1            ACTIVE                 VERIFIED     GANTT   
210167          1            ACTIVE                 VERIFIED     GANTT   
210168          1            ACTIVE                 VERIFIED     GANTT   

       first_name middle_name  res_street_address res_city_desc state_cd  \
210162       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210163       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210164       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210165       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210166       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210167       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   
210168       JACK     DOUGLAS  4651  ANDREA LN       BURLINGTON       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
210162   27215.0         U          UN      REP           M         78   
210163   27215.0         U          UN      REP           M         78   
210164   27215.0         U          UN      REP           M         78   
210165   27215.0         U          UN      REP           M         78   
210166   27215.0         U          UN      REP           M         78   
210167   27215.0         U          UN      REP           M         78   
210168   27215.0         U          UN      REP           M         78   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
210162          OR           N  09/29/1973             02             13.0   
210163          OR           N  09/29/1973             02             13.0   
210164          OR           N  09/29/1973             02             13.0   
210165          OR           N  09/29/1973             02             13.0   
210166          OR           N  09/29/1973             02             13.0   
210167          OR           N  09/29/1973             02             13.0   
210168          OR           N  09/29/1973             02             13.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
210162               15A              15A             24.0            64.0   
210163               15A              15A             24.0            64.0   
210164               15A              15A             24.0            64.0   
210165               15A              15A             24.0            64.0   
210166               15

ncid       election_desc  voter_reg_num election_lbl  \
232831  AA174391  11/03/2020 GENERAL     10191737.0   2020-11-03   
232832  AA174391  11/06/2018 GENERAL     10191737.0   2018-11-06   
232833  AA174391  11/08/2016 GENERAL     10191737.0   2016-11-08   
232834  AA174391  11/04/2014 GENERAL     10191737.0   2014-11-04   
232835  AA174391  11/06/2012 GENERAL     10191737.0   2012-11-06   
232836  AA174391  11/06/2012 GENERAL     10191737.0   2012-11-06   
232837  AA174391                None            NaN          NaT   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
232831  ABSENTEE ONESTOP            DEM       H25             41.0       H25   
232832         IN-PERSON            DEM       H25             41.0       H25   
232833  ABSENTEE ONESTOP            DEM       146             60.0       146   
232834         IN-PERSON            DEM       146             60.0       146   
232835         IN-PERSON            DEM       064              1.0       064   
232836  ABSENTEE ONESTOP            DEM       146             60.0       146   
232837               NaN            NaN       NaN              NaN       NaN   

        county_id voter_status_desc voter_status_reason_desc last_name  \
232831         41            ACTIVE                 VERIFIED    WARREN   
232832         41            ACTIVE                 VERIFIED    WARREN   
232833         41            ACTIVE                 VERIFIED    WARREN   
232834         41            ACTIVE                 VERIFIED    WARREN   
232835         41            ACTIVE                 VERIFIED    WARREN   
232836         41            ACTIVE                 VERIFIED    WARREN   
232837         41            ACTIVE                 VERIFIED    WARREN   

       first_name middle_name res_street_address res_city_desc state_cd  \
232831     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232832     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232833     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232834     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232835     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232836     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   
232837     LATOYA      DIONNE  4388  KELSO DR       HIGH POINT       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
232831   27265.0         B          NL      DEM           F         42   
232832   27265.0         B          NL      DEM           F         42   
232833   27265.0         B          NL      DEM           F         42   
232834   27265.0         B          NL      DEM           F         42   
232835   27265.0         B          NL      DEM           F         42   
232836   27265.0         B          NL      DEM           F         42   
232837   27265.0         B          NL      DEM           F         42   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
232831          NC           Y  10/14/2016            H25              6.0   
232832          NC           Y  10/14/2016            H25              6.0   
232833          NC           Y  10/14/2016            H25              6.0   
232834          NC           Y  10/14/2016            H25              6.0   
232835          NC           Y  10/14/2016            H25              6.0   
232836          NC           Y  10/14/2016            H25              6.0   
232837          NC           Y  10/14/2016            H25              6.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
232831               18B               18             27.0            62.0   
232832               18B               18             27.0            62.0   
232833               18B               18             27.0            62.0   
232834               18B               18             27.0            62.0   
232835               18B

ncid       election_desc  voter_reg_num election_lbl  \
566390  AB14598  11/03/2020 GENERAL            NaN          NaT   
566391  AB14598  11/06/2018 GENERAL            NaN          NaT   
566392  AB14598  11/08/2016 GENERAL        32922.0   2016-11-08   
566393  AB14598  11/04/2014 GENERAL        32922.0   2014-11-04   
566394  AB14598  11/06/2012 GENERAL        32922.0   2012-11-06   
566395  AB14598  11/06/2012 GENERAL        32922.0   2012-11-06   
566396  AB14598                None            NaN          NaT   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
566390               NaN            NaN       NaN              NaN       NaN   
566391               NaN            NaN       NaN              NaN       NaN   
566392         IN-PERSON            DEM      LILE              4.0      LILE   
566393  ABSENTEE ONESTOP            DEM      LILE              4.0      LILE   
566394         IN-PERSON            REP        B2              2.0        B2   
566395  ABSENTEE ONESTOP            DEM      LILE              4.0      LILE   
566396               NaN            NaN       NaN              NaN       NaN   

        county_id voter_status_desc voter_status_reason_desc last_name  \
566390          4            ACTIVE                 VERIFIED     SMITH   
566391          4            ACTIVE                 VERIFIED     SMITH   
566392          4            ACTIVE                 VERIFIED     SMITH   
566393          4            ACTIVE                 VERIFIED     SMITH   
566394          4            ACTIVE                 VERIFIED     SMITH   
566395          4            ACTIVE                 VERIFIED     SMITH   
566396          4            ACTIVE                 VERIFIED     SMITH   

       first_name middle_name  res_street_address res_city_desc state_cd  \
566390    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566391    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566392    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566393    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566394    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566395    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   
566396    ANTHONY        DALE  115 S SECOND ST       LILESVILLE       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
566390   28091.0         B          UN      DEM           M         49   
566391   28091.0         B          UN      DEM           M         49   
566392   28091.0         B          UN      DEM           M         49   
566393   28091.0         B          UN      DEM           M         49   
566394   28091.0         B          UN      DEM           M         49   
566395   28091.0         B          UN      DEM           M         49   
566396   28091.0         B          UN      DEM           M         49   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
566390          NC           Y  11/02/2012           LILE              9.0   
566391          NC           Y  11/02/2012           LILE              9.0   
566392          NC           Y  11/02/2012           LILE              9.0   
566393          NC           Y  11/02/2012           LILE              9.0   
566394          NC           Y  11/02/2012           LILE              9.0   
566395          NC           Y  11/02/2012           LILE              9.0   
566396          NC           Y  11/02/2012           LILE              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
566390               16A              16A             25.0            55.0   
566391               16A              16A             25.0            55.0   
566392               16A              16A             25.0            55.0   
566393               16A              16A             25.0            55.0   
566394               16

ncid       election_desc  voter_reg_num election_lbl  \
581499  AB22129  11/03/2020 GENERAL        25981.0   2020-11-03   
581500  AB22129  11/06/2018 GENERAL        25981.0   2018-11-06   
581501  AB22129  11/08/2016 GENERAL        25981.0   2016-11-08   
581502  AB22129  11/04/2014 GENERAL        25981.0   2014-11-04   
581503  AB22129  11/06/2012 GENERAL        25981.0   2012-11-06   
581504  AB22129  11/06/2012 GENERAL        25981.0   2012-11-06   
581505  AB22129                None            NaN          NaT   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
581499  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
581500  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
581501  ABSENTEE ONESTOP            UNA        B1              2.0        B1   
581502  ABSENTEE ONESTOP            REP        B1              2.0        B1   
581503  ABSENTEE ONESTOP            REP        B1              2.0        B1   
581504         IN-PERSON            REP        26             18.0        26   
581505               NaN            NaN       NaN              NaN       NaN   

        county_id voter_status_desc voter_status_reason_desc last_name  \
581499          2            ACTIVE                 VERIFIED    LYERLY   
581500          2            ACTIVE                 VERIFIED    LYERLY   
581501          2            ACTIVE                 VERIFIED    LYERLY   
581502          2            ACTIVE                 VERIFIED    LYERLY   
581503          2            ACTIVE                 VERIFIED    LYERLY   
581504          2            ACTIVE                 VERIFIED    LYERLY   
581505          2            ACTIVE                 VERIFIED    LYERLY   

       first_name middle_name  res_street_address res_city_desc state_cd  \
581499    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581500    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581501    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581502    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581503    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581504    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   
581505    WINSTON      COBURN  58  LINKSIDE LN          HICKORY       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
581499   28601.0         W          NL      UNA           M         51   
581500   28601.0         W          NL      UNA           M         51   
581501   28601.0         W          NL      UNA           M         51   
581502   28601.0         W          NL      UNA           M         51   
581503   28601.0         W          NL      UNA           M         51   
581504   28601.0         W          NL      UNA           M         51   
581505   28601.0         W          NL      UNA           M         51   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
581499          NC           Y  09/20/1995             B1              5.0   
581500          NC           Y  09/20/1995             B1              5.0   
581501          NC           Y  09/20/1995             B1              5.0   
581502          NC           Y  09/20/1995             B1              5.0   
581503          NC           Y  09/20/1995             B1              5.0   
581504          NC           Y  09/20/1995             B1              5.0   
581505          NC           Y  09/20/1995             B1              5.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
581499               22A              22A             42.0            94.0   
581500               22A              22A             42.0            94.0   
581501               22A              22A             42.0            94.0   
581502               22A              22A             42.0            94.0   
581503               22

ncid       election_desc  voter_reg_num election_lbl  \
761860  AD24600  11/03/2020 GENERAL            NaN          NaT   
761861  AD24600  11/06/2018 GENERAL        36708.0   2018-11-06   
761862  AD24600  11/08/2016 GENERAL        36708.0   2016-11-08   
761863  AD24600  11/08/2016 GENERAL        36708.0   2016-11-08   
761864  AD24600  11/04/2014 GENERAL            NaN          NaT   
761865  AD24600  11/06/2012 GENERAL        36708.0   2012-11-06   
761866  AD24600                None            NaN          NaT   

           voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
761860               NaN            NaN       NaN              NaN       NaN   
761861         IN-PERSON            DEM      BURN              4.0      BURN   
761862       PROVISIONAL            DEM      BURN              4.0      BURN   
761863       PROVISIONAL            NaN      BURN              4.0      BURN   
761864               NaN            NaN       NaN              NaN       NaN   
761865  ABSENTEE ONESTOP            DEM      0007             84.0      0007   
761866               NaN            NaN       NaN              NaN       NaN   

        county_id voter_status_desc   voter_status_reason_desc last_name  \
761860          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761861          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761862          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761863          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761864          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761865          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   
761866          4          INACTIVE  CONFIRMATION NOT RETURNED  STREATER   

       first_name middle_name res_street_address res_city_desc state_cd  \
761860     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761861     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761862     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761863     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761864     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761865     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   
761866     TERESA     LAWUANA     157  IVY RD          POLKTON       NC   

        zip_code race_code ethnic_code party_cd gender_code  birth_age  \
761860   28135.0         U          UN      DEM           F         59   
761861   28135.0         U          UN      DEM           F         59   
761862   28135.0         U          UN      DEM           F         59   
761863   28135.0         U          UN      DEM           F         59   
761864   28135.0         U          UN      DEM           F         59   
761865   28135.0         U          UN      DEM           F         59   
761866   28135.0         U          UN      DEM           F         59   

       birth_state drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv  \
761860          NC           Y  11/08/2016           BURN              9.0   
761861          NC           Y  11/08/2016           BURN              9.0   
761862          NC           Y  11/08/2016           BURN              9.0   
761863          NC           Y  11/08/2016           BURN              9.0   
761864          NC           Y  11/08/2016           BURN              9.0   
761865          NC           Y  11/08/2016           BURN              9.0   
761866          NC           Y  11/08/2016           BURN              9.0   

       super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv  \
761860               16A              16A             25.0            55.0   
761861               16A              16A             25.0            55.0   
761862               16A              16A             25.0            55.0   
761863               16A              16A             25.0            55.0   
761864         

...

ncid       election_desc  voter_reg_num election_lbl  \
38383374  EP21414  11/03/2020 GENERAL        27375.0   2020-11-03   
38383375  EP21414  11/06/2018 GENERAL        27375.0   2018-11-06   
38383376  EP21414  11/08/2016 GENERAL        27375.0   2016-11-08   
38383377  EP21414  11/04/2014 GENERAL        27375.0   2014-11-04   
38383378  EP21414  11/06/2012 GENERAL        27375.0   2012-11-06   
38383379  EP21414  11/06/2012 GENERAL        27375.0   2012-11-06   
38383380  EP21414                None            NaN          NaT   

             voting_method voted_party_cd pct_label  voted_county_id  \
38383374  ABSENTEE ONESTOP            REP      PRGA             98.0   
38383375  ABSENTEE ONESTOP            REP      PRGA             98.0   
38383376  ABSENTEE ONESTOP            REP      PRGA             98.0   
38383377         IN-PERSON            REP      0035             64.0   
38383378  ABSENTEE ONESTOP            DEM      PRCR             98.0   
38383379  ABSENTEE ONESTOP            REP      0035             64.0   
38383380               NaN            NaN       NaN              NaN   

         vtd_label  county_id voter_status_desc voter_status_reason_desc  \
38383374      PRGA         98            ACTIVE                 VERIFIED   
38383375      PRGA         98            ACTIVE                 VERIFIED   
38383376      PRGA         98            ACTIVE                 VERIFIED   
38383377      0035         98            ACTIVE                 VERIFIED   
38383378      PRCR         98            ACTIVE                 VERIFIED   
38383379      0035         98            ACTIVE                 VERIFIED   
38383380       NaN         98            ACTIVE                 VERIFIED   

         last_name first_name middle_name         res_street_address  \
38383374    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383375    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383376    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383377    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383378    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383379    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     
38383380    WATSON     BRENDA      BAILEY  4300  US HWY 264 ALT  E     

         res_city_desc state_cd  zip_code race_code ethnic_code party_cd  \
38383374        WILSON       NC   27893.0         W          NL      REP   
38383375        WILSON       NC   27893.0         W          NL      REP   
38383376        WILSON       NC   27893.0         W          NL      REP   
38383377        WILSON       NC   27893.0         W          NL      REP   
38383378        WILSON       NC   27893.0         W          NL      REP   
38383379        WILSON       NC   27893.0         W          NL      REP   
38383380        WILSON       NC   27893.0         W          NL      REP   

         gender_code  birth_age birth_state drivers_lic  registr_dt  \
38383374           F         72          NC           Y  10/09/1968   
38383375           F         72          NC           Y  10/09/1968   
38383376           F         72          NC           Y  10/09/1968   
38383377           F         72          NC           Y  10/09/1968   
38383378           F         72          NC           Y  10/09/1968   
38383379           F         72          NC           Y  10/09/1968   
38383380           F         72          NC           Y  10/09/1968   

         precinct_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
38383374           PRGA              1.0               07B               07   
38383375           PRGA              1.0               07B               07   
38383376           PRGA              1.0               07B               07   
38383377           PRGA              1.0               07B               07   
38383378           PRGA              1.0               07B               07   
38383379           PRGA              1.0     

ncid       election_desc  voter_reg_num election_lbl  \
38445457  EP46816  11/03/2020 GENERAL    757513184.0   2020-11-03   
38445458  EP46816  11/06/2018 GENERAL            NaN          NaT   
38445459  EP46816  11/08/2016 GENERAL    757513184.0   2016-11-08   
38445460  EP46816  11/04/2014 GENERAL    757513184.0   2014-11-04   
38445461  EP46816  11/06/2012 GENERAL    757513184.0   2012-11-06   
38445462  EP46816  11/06/2012 GENERAL    757513184.0   2012-11-06   
38445463  EP46816                None            NaN          NaT   

             voting_method voted_party_cd pct_label  voted_county_id  \
38445457  ABSENTEE ONESTOP            REP      PRTA             98.0   
38445458               NaN            NaN       NaN              NaN   
38445459         IN-PERSON            REP        16             10.0   
38445460         IN-PERSON            REP        16             10.0   
38445461  ABSENTEE ONESTOP            DEM      PRGA             98.0   
38445462         IN-PERSON            REP        16             10.0   
38445463               NaN            NaN       NaN              NaN   

         vtd_label  county_id voter_status_desc voter_status_reason_desc  \
38445457      PRTA         98            ACTIVE                 VERIFIED   
38445458       NaN         98            ACTIVE                 VERIFIED   
38445459        16         98            ACTIVE                 VERIFIED   
38445460        16         98            ACTIVE                 VERIFIED   
38445461      PRGA         98            ACTIVE                 VERIFIED   
38445462        16         98            ACTIVE                 VERIFIED   
38445463       NaN         98            ACTIVE                 VERIFIED   

         last_name first_name middle_name           res_street_address  \
38445457     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445458     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445459     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445460     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445461     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445462     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   
38445463     ELLIS  FREDERICK       WAYNE  4113  BELAND AVE NW  #APT-A   

         res_city_desc state_cd  zip_code race_code ethnic_code party_cd  \
38445457        WILSON       NC   27896.0         W          UN      REP   
38445458        WILSON       NC   27896.0         W          UN      REP   
38445459        WILSON       NC   27896.0         W          UN      REP   
38445460        WILSON       NC   27896.0         W          UN      REP   
38445461        WILSON       NC   27896.0         W          UN      REP   
38445462        WILSON       NC   27896.0         W          UN      REP   
38445463        WILSON       NC   27896.0         W          UN      REP   

         gender_code  birth_age birth_state drivers_lic  registr_dt  \
38445457           M         70          NC           Y  01/22/2019   
38445458           M         70          NC           Y  01/22/2019   
38445459           M         70          NC           Y  01/22/2019   
38445460           M         70          NC           Y  01/22/2019   
38445461           M         70          NC           Y  01/22/2019   
38445462           M         70          NC           Y  01/22/2019   
38445463           M         70          NC           Y  01/22/2019   

         precinct_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
38445457           PRTA              1.0               07C               07   
38445458           PRTA              1.0               07C               07   
38445459           PRTA              1.0               07C               07   
38445460           PRTA              1.0               07C               07   
38445461           PRTA              1.0               07C               07   
38445462           PRTA      

ncid       election_desc  voter_reg_num election_lbl  \
38552252  EP80424  11/03/2020 GENERAL            NaN          NaT   
38552253  EP80424  11/06/2018 GENERAL    757480595.0   2018-11-06   
38552254  EP80424  11/08/2016 GENERAL    757480595.0   2016-11-08   
38552255  EP80424  11/04/2014 GENERAL    757480595.0   2014-11-04   
38552256  EP80424  11/06/2012 GENERAL    757480595.0   2012-11-06   
38552257  EP80424  11/06/2012 GENERAL    757480595.0   2012-11-06   
38552258  EP80424                None            NaN          NaT   

             voting_method voted_party_cd pct_label  voted_county_id  \
38552252               NaN            NaN       NaN              NaN   
38552253         IN-PERSON            DEM      PRSP             98.0   
38552254         IN-PERSON            DEM      PRSP             98.0   
38552255         IN-PERSON            DEM      PRSP             98.0   
38552256  ABSENTEE ONESTOP            DEM       4-B             70.0   
38552257  ABSENTEE ONESTOP            DEM      PRSP             98.0   
38552258               NaN            NaN       NaN              NaN   

         vtd_label  county_id voter_status_desc voter_status_reason_desc  \
38552252       NaN         98            ACTIVE                 VERIFIED   
38552253      PRSP         98            ACTIVE                 VERIFIED   
38552254      PRSP         98            ACTIVE                 VERIFIED   
38552255      PRSP         98            ACTIVE                 VERIFIED   
38552256       4-B         98            ACTIVE                 VERIFIED   
38552257      PRSP         98            ACTIVE                 VERIFIED   
38552258       NaN         98            ACTIVE                 VERIFIED   

         last_name  first_name middle_name           res_street_address  \
38552252      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552253      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552254      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552255      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552256      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552257      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      
38552258      PITT  STEPFERNIA         NaN  9016  ST MARYS CHURCH RD      

         res_city_desc state_cd  zip_code race_code ethnic_code party_cd  \
38552252         KENLY       NC   27542.0         B          NL      DEM   
38552253         KENLY       NC   27542.0         B          NL      DEM   
38552254         KENLY       NC   27542.0         B          NL      DEM   
38552255         KENLY       NC   27542.0         B          NL      DEM   
38552256         KENLY       NC   27542.0         B          NL      DEM   
38552257         KENLY       NC   27542.0         B          NL      DEM   
38552258         KENLY       NC   27542.0         B          NL      DEM   

         gender_code  birth_age birth_state drivers_lic  registr_dt  \
38552252           M         32          MD           Y  09/30/2008   
38552253           M         32          MD           Y  09/30/2008   
38552254           M         32          MD           Y  09/30/2008   
38552255           M         32          MD           Y  09/30/2008   
38552256           M         32          MD           Y  09/30/2008   
38552257           M         32          MD           Y  09/30/2008   
38552258           M         32          MD           Y  09/30/2008   

         precinct_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
38552252           PRSP              1.0               07C               07   
38552253           PRSP              1.0               07C               07   
38552254           PRSP              1.0               07C               07   
38552255           PRSP              1.0               07C               07   
38552256           PRSP              1.0               07C               07   
38552257           PR

ncid       election_desc  voter_reg_num election_lbl  \
38643075  ER15626  11/03/2020 GENERAL        15048.0   2020-11-03   
38643076  ER15626  11/06/2018 GENERAL        15048.0   2018-11-06   
38643077  ER15626  11/08/2016 GENERAL        15048.0   2016-11-08   
38643078  ER15626  11/08/2016 GENERAL        15048.0   2016-11-08   
38643079  ER15626  11/04/2014 GENERAL        15048.0   2014-11-04   
38643080  ER15626  11/04/2014 GENERAL        15048.0   2014-11-04   
38643081  ER15626  11/06/2012 GENERAL        15048.0   2012-11-06   
38643082  ER15626  11/06/2012 GENERAL        15048.0   2012-11-06   
38643083  ER15626                None            NaN          NaT   

             voting_method voted_party_cd pct_label  voted_county_id  \
38643075  ABSENTEE ONESTOP            REP      SFAL             99.0   
38643076  ABSENTEE ONESTOP            REP      SFAL             99.0   
38643077         IN-PERSON            REP      SFAL             99.0   
38643078  ABSENTEE ONESTOP            REP       133             34.0   
38643079         IN-PERSON            REP      SFAL             99.0   
38643080         IN-PERSON            REP       133             34.0   
38643081  ABSENTEE ONESTOP            REP      SFAL             99.0   
38643082  ABSENTEE BY MAIL            REP       133             34.0   
38643083               NaN            NaN       NaN              NaN   

         vtd_label  county_id voter_status_desc voter_status_reason_desc  \
38643075      SFAL         99            ACTIVE                 VERIFIED   
38643076      SFAL         99            ACTIVE                 VERIFIED   
38643077      SFAL         99            ACTIVE                 VERIFIED   
38643078       133         99            ACTIVE                 VERIFIED   
38643079      SFAL         99            ACTIVE                 VERIFIED   
38643080       133         99            ACTIVE                 VERIFIED   
38643081      SFAL         99            ACTIVE                 VERIFIED   
38643082       133         99            ACTIVE                 VERIFIED   
38643083       NaN         99            ACTIVE                 VERIFIED   

         last_name first_name middle_name   res_street_address res_city_desc  \
38643075  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643076  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643077  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643078  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643079  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643080  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643081  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643082  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   
38643083  WILLIAMS      TRACY     MICHELE  2521  ROCKETT RD        EAST BEND   

         state_cd  zip_code race_code ethnic_code party_cd gender_code  \
38643075       NC   27018.0         W          NL      REP           F   
38643076       NC   27018.0         W          NL      REP           F   
38643077       NC   27018.0         W          NL      REP           F   
38643078       NC   27018.0         W          NL      REP           F   
38643079       NC   27018.0         W          NL      REP           F   
38643080       NC   27018.0         W          NL      REP           F   
38643081       NC   27018.0         W          NL      REP           F   
38643082       NC   27018.0         W          NL      REP           F   
38643083       NC   27018.0         W          NL      REP           F   

          birth_age birth_state drivers_lic  registr_dt precinct_abbrv  \
38643075         52          NC           Y  03/09/1988           SFAL   
38643076         52          NC           Y  03/09/1988           SFAL   
38643077         52          NC           Y  03/09/1988           SFAL   
38

ncid       election_desc  voter_reg_num election_lbl  \
38738496  ER43863  11/03/2020 GENERAL        79756.0   2020-11-03   
38738497  ER43863  11/06/2018 GENERAL        79756.0   2018-11-06   
38738498  ER43863  11/06/2018 GENERAL        79756.0   2018-11-06   
38738499  ER43863  11/08/2016 GENERAL            NaN          NaT   
38738500  ER43863  11/04/2014 GENERAL            NaN          NaT   
38738501  ER43863  11/06/2012 GENERAL            NaN          NaT   
38738502  ER43863                None            NaN          NaT   

             voting_method voted_party_cd pct_label  voted_county_id  \
38738496  ABSENTEE ONESTOP            REP      BNVL             99.0   
38738497  ABSENTEE ONESTOP            REP      BNVL             99.0   
38738498  ABSENTEE ONESTOP            REP      1507             74.0   
38738499               NaN            NaN       NaN              NaN   
38738500               NaN            NaN       NaN              NaN   
38738501               NaN            NaN       NaN              NaN   
38738502               NaN            NaN       NaN              NaN   

         vtd_label  county_id voter_status_desc voter_status_reason_desc  \
38738496      BNVL         99            ACTIVE                 VERIFIED   
38738497      BNVL         99            ACTIVE                 VERIFIED   
38738498      1507         99            ACTIVE                 VERIFIED   
38738499       NaN         99            ACTIVE                 VERIFIED   
38738500       NaN         99            ACTIVE                 VERIFIED   
38738501       NaN         99            ACTIVE                 VERIFIED   
38738502       NaN         99            ACTIVE                 VERIFIED   

         last_name first_name middle_name res_street_address res_city_desc  \
38738496     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738497     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738498     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738499     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738500     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738501     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   
38738502     DAVIS     DENVER       SMITH   1200  MEAD RD        BOONVILLE   

         state_cd  zip_code race_code ethnic_code party_cd gender_code  \
38738496       NC   27011.0         W          NL      REP           M   
38738497       NC   27011.0         W          NL      REP           M   
38738498       NC   27011.0         W          NL      REP           M   
38738499       NC   27011.0         W          NL      REP           M   
38738500       NC   27011.0         W          NL      REP           M   
38738501       NC   27011.0         W          NL      REP           M   
38738502       NC   27011.0         W          NL      REP           M   

          birth_age birth_state drivers_lic  registr_dt precinct_abbrv  \
38738496         22          NC           Y  11/02/2018           BNVL   
38738497         22          NC           Y  11/02/2018           BNVL   
38738498         22          NC           Y  11/02/2018           BNVL   
38738499         22          NC           Y  11/02/2018           BNVL   
38738500         22          NC           Y  11/02/2018           BNVL   
38738501         22          NC           Y  11/02/2018           BNVL   
38738502         22          NC           Y  11/02/2018           BNVL   

          cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
38738496             10.0                23               23             34.0   
38738497             10.0                23               23             34.0   
38738498             10.0                23               23             34.0   
38738499             10.0                23               23             34.0   
38738500             10.0                23               

> Because several of these ncids have conflicts in more than one election and because it is not possible to verify which records may be correct, these 310 ncids will be dropped from analysis.

In [15]:
#########################################################################
# Drop the following rows to deal with duplicate votes cast by same ncid 
# in same election:
#########################################################################

## Drop all record for all ncids that have duplicates in any major election
voter_elecs.drop(index=voter_elecs.loc[voter_elecs['ncid'].isin(dup_ncid_elecs['ncid'].unique())].index,
                inplace=True)

In [16]:
## Check that all duplicates have been successfully dealt with
voter_elecs.duplicated(subset=['ncid', 'election_desc']).sum()

0

In [17]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_no_dup_ncids.gz',
#                    compression='gzip', index=False)

## Engineer Features for Grouping and Modeling

In [27]:
## Load in NC statewide voter history and info by election
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_no_dup_ncids.gz',
                          dtype={'voting_method': str,
                                 'voted_party_cd': str,
                                 'pct_label': str,
                                 'vtd_label': str,
                                 'precinct_abbrv': str, 
                                 'super_court_abbrv': str, 
                                 'judic_dist_abbrv': str,
                                 'school_dist_abbrv': str,
                                 'vtd_abbrv': str
                                },
                          parse_dates=['election_lbl']
                         )

In [28]:
voter_elecs.head(20)

ncid       election_desc  voter_reg_num election_lbl  \
0   AA100000  11/03/2020 GENERAL      9050398.0   2020-11-03   
1   AA100000  11/06/2018 GENERAL            NaN          NaT   
2   AA100000  11/08/2016 GENERAL      9050398.0   2016-11-08   
3   AA100000  11/04/2014 GENERAL            NaN          NaT   
4   AA100000  11/06/2012 GENERAL            NaN          NaT   
5   AA100000                None            NaN          NaT   
6   AA100006  11/03/2020 GENERAL      9050405.0   2020-11-03   
7   AA100006  11/06/2018 GENERAL      9050405.0   2018-11-06   
8   AA100006  11/08/2016 GENERAL      9050405.0   2016-11-08   
9   AA100006  11/04/2014 GENERAL      9050405.0   2014-11-04   
10  AA100006  11/06/2012 GENERAL      9050405.0   2012-11-06   
11  AA100006                None            NaN          NaT   
12  AA100007  11/03/2020 GENERAL      9050406.0   2020-11-03   
13  AA100007  11/06/2018 GENERAL      9050406.0   2018-11-06   
14  AA100007  11/08/2016 GENERAL      9050406.0   2016-11-08   
15  AA100007  11/04/2014 GENERAL      9050406.0   2014-11-04   
16  AA100007  11/06/2012 GENERAL      9050406.0   2012-11-06   
17  AA100007                None            NaN          NaT   
18  AA100008  11/03/2020 GENERAL            NaN          NaT   
19  AA100008  11/06/2018 GENERAL            NaN          NaT   

       voting_method voted_party_cd pct_label  voted_county_id vtd_label  \
0   ABSENTEE ONESTOP            UNA        07              1.0        07   
1                NaN            NaN       NaN              NaN       NaN   
2   ABSENTEE ONESTOP            UNA        07              1.0        07   
3                NaN            NaN       NaN              NaN       NaN   
4                NaN            NaN       NaN              NaN       NaN   
5                NaN            NaN       NaN              NaN       NaN   
6   ABSENTEE ONESTOP            REP       09S              1.0       09S   
7          IN-PERSON            REP       09S              1.0       09S   
8   ABSENTEE ONESTOP            REP       09S              1.0       09S   
9          IN-PERSON            REP       09S              1.0       09S   
10  ABSENTEE ONESTOP            REP       09S              1.0       09S   
11               NaN            NaN       NaN              NaN       NaN   
12  ABSENTEE BY MAIL            UNA       06E              1.0       06E   
13  ABSENTEE BY MAIL            UNA       06E              1.0       06E   
14  ABSENTEE BY MAIL            UNA       06E              1.0       06E   
15  ABSENTEE BY MAIL            UNA       06E              1.0       06E   
16  ABSENTEE BY MAIL            UNA       06E              1.0       06E   
17               NaN            NaN       NaN              NaN       NaN   
18               NaN            NaN       NaN              NaN       NaN   
19               NaN            NaN       NaN              NaN       NaN   

    county_id voter_status_desc voter_status_reason_desc last_name first_name  \
0           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
1           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
2           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
3           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
4           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
5           1            ACTIVE                 VERIFIED  BOYDSTUN      JAMES   
6           1            ACTIVE                 VERIFIED    BROOKS     DENISE   
7           1            ACTIVE                 VERIFIED    BROOKS     DENISE   
8           1            ACTIVE                 VERIFIED    BROOKS     DENISE   
9           1            ACTIVE                 VERIFIED    BROOKS     DENISE   
10          1            ACTIVE                 VERIFIED    BROOKS     DENISE   
11          1            ACTIVE                 VERIFIED    BROOKS     DENISE   
12          1

In [29]:
voter_elecs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 44344680 entries, 0 to 44344679
Data columns (total 38 columns):
ncid                        object
election_desc               object
voter_reg_num               float64
election_lbl                datetime64[ns]
voting_method               object
voted_party_cd              object
pct_label                   object
voted_county_id             float64
vtd_label                   object
county_id                   int64
voter_status_desc           object
voter_status_reason_desc    object
last_name                   object
first_name                  object
middle_name                 object
res_street_address          object
res_city_desc               object
state_cd                    object
zip_code                    float64
race_code                   object
ethnic_code                 object
party_cd                    object
gender_code                 object
birth_age                   int64
birth_state                 object
d

In [31]:
## Recast election_lbl as datetime
voter_elecs['election_lbl'] = pd.to_datetime(
    voter_elecs['election_desc'].str.split(' ',
                                           n=1).apply(
        # Where election_desc is 'None' fill with NaN
        lambda x: x[0]).replace({'None':np.nan}))

# ## Create a new col for just the year
# voter_elecs.insert(loc=4, column='election_yr',
#                  value=voter_elecs['election_lbl'].dt.year)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "pandas/_libs/tslib.pyx", line 2270, in pandas._libs.tslib.array_to_datetime
  File "pandas/_libs/src/datetime.pxd", line 119, in datetime._string_to_dts
ValueError: Error parsing datetime string "11/08/2016" at position 2

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/maxsteele/opt/anaconda3/envs/learn-env/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 3326, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-31-575285e13b19>", line 6, in <module>
    lambda x: x[0]).replace({'None':np.nan}))
  File "/Users/maxsteele/opt/anaconda3/envs/learn-env/lib/python3.6/site-packages/pandas/core/tools/datetimes.py", line 373, in to_datetime
    values = _convert_listlike(arg._values, True, format)
  File "/Users/maxsteele/opt/anaconda3/envs/learn-env/lib/python3.6/site-packages/pandas/core/tools/datetimes.py", line 294, in _c

TypeError: must be str, not list

In [ ]:
## Create a binary variable indicating whether or not in individual registered
  ## in time to vote in that election

# Calculate normal registration deadline for the election
  # (25 days before election in NC, but afterwards have option to register 
  #  in person during early voting period)
voter_elecs.insert(loc=4, column='registr_deadline',
                 value=pd.to_datetime(voter_elecs['election_lbl'] - dt.timedelta(days=25)))

# Recast voter registration date as datetime variable 
voter_elecs['registr_dt'] = pd.to_datetime(voter_elecs['registr_dt'])

# Check whether or not an individual voted (if they did, they were registered
  # in time and may have registered in person after the normal deadline) and
  # compare registration date to registration deadline
voter_elecs.insert(loc=5, column='registr_in_time',
                 value=np.where(((voter_elecs['voting_method'].isna()) & 
                                 (voter_elecs['registr_dt'] > voter_elecs['registr_deadline'])),
                                0,1))

In [ ]:
## Drop registr_deadline column
voter_elecs.drop(columns=['registr_deadline'], inplace=True)

In [ ]:
## Create a column for age adjusted according to the specific election year
voter_elecs.insert(loc=5, column='birth_age_adj',
                   value=voter_elecs['election_lbl'].dt.year.subtract(voter_elecs['birth_year']))

In [ ]:
## Group original vote methods into more general categories in a new variable
 # Map the original categoriess to new ones
vote_method_map = {'ABSENTEE ONESTOP': 'Early',
                   'IN-PERSON': 'Election Day',
                   'ABSENTEE BY MAIL': 'Early',
                   'ABSENTEE CURBSIDE': 'Early',
                   'TRANSFER': 'Other',
                   'PROVISIONAL': 'Other',
                   'CURBSIDE': 'Election Day'}

# Apply the map to create new vote_method_cat column
voter_elecs.insert(loc=7, column='vote_method_cat',
                 value=voter_elecs['voting_method'].map(vote_method_map))

In [ ]:
## Inspect updated df
voter_elecs.head(35)

In [24]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

## Create a DataFrame Summarizing Each Voter's History

In [ ]:
## Aggregate individual ncid's to find a way to easily identify individuals
  ## with no recent voting history
ncid_grp_sum = voter_elecs.groupby('ncid').sum().reset_index()
ncid_grp_sum.head(20)

In [ ]:
## Inspect record for an individual with no recent voting history
ncid_grp_sum.loc[ncid_grp_sum['ncid']=='AL261840']
## voter_reg_num shows up as 0 when an individual has no voting history

In [ ]:
## 990,485 voters currently registered in NC have not voted in a 
## major election so far
never_voted_maj_elec = ncid_grp_sum.loc[ncid_grp_sum['voter_reg_num']==0][['ncid']]
len(never_voted_maj_elec)

In [28]:
## Insert a binary column indicating that a voter has no history for voting
  ## in recent major elections (1) or has recently voted at least once (0)
voter_elecs.insert(loc=2, column='no_vote_his',
                 value=np.where(voter_elecs['ncid'].isin(never_voted_maj_elec['ncid']),
                               1,0))

In [ ]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

In [29]:
## Set multiindex for df grouping first by ncid, then election_desc
voter_elecs_mi = voter_elecs.set_index(['ncid','election_desc'])
voter_elecs_mi.head()

no_vote_his  county_id  voter_reg_num  \
ncid    election_desc                                               
AA56273 11/03/2020 GENERAL            0        1.0      9005990.0   
        11/06/2018 GENERAL            0        1.0      9005990.0   
        11/08/2016 GENERAL            0        1.0      9005990.0   
        11/04/2014 GENERAL            0        1.0      9005990.0   
        11/06/2012 GENERAL            0        1.0      9005990.0   

                           election_lbl  registr_in_time  birth_age_adj  \
ncid    election_desc                                                     
AA56273 11/03/2020 GENERAL   2020-11-03                1           85.0   
        11/06/2018 GENERAL   2018-11-06                1           83.0   
        11/08/2016 GENERAL   2016-11-08                1           81.0   
        11/04/2014 GENERAL   2014-11-04                1           79.0   
        11/06/2012 GENERAL   2012-11-06                1           77.0   

                               voting_method vote_method_cat voted_party_cd  \
ncid    election_desc                                                         
AA56273 11/03/2020 GENERAL  ABSENTEE BY MAIL           Early            UNA   
        11/06/2018 GENERAL         IN-PERSON    Election Day            UNA   
        11/08/2016 GENERAL         IN-PERSON    Election Day            UNA   
        11/04/2014 GENERAL         IN-PERSON    Election Day            UNA   
        11/06/2012 GENERAL         IN-PERSON    Election Day            UNA   

                           pct_label  voted_county_id vtd_label  \
ncid    election_desc                                             
AA56273 11/03/2020 GENERAL       08N              1.0       08N   
        11/06/2018 GENERAL       08N              1.0       08N   
        11/08/2016 GENERAL       08N              1.0       08N   
        11/04/2014 GENERAL       08N              1.0       08N   
        11/06/2012 GENERAL       08N              1.0       08N   

                           voter_status_desc voter_status_reason_desc  \
ncid    election_desc                                                   
AA56273 11/03/2020 GENERAL            ACTIVE                 VERIFIED   
        11/06/2018 GENERAL            ACTIVE                 VERIFIED   
        11/08/2016 GENERAL            ACTIVE                 VERIFIED   
        11/04/2014 GENERAL            ACTIVE                 VERIFIED   
        11/06/2012 GENERAL            ACTIVE                 VERIFIED   

                           last_name first_name middle_name  \
ncid    election_desc                                         
AA56273 11/03/2020 GENERAL     AABEL       RUTH      EVELYN   
        11/06/2018 GENERAL     AABEL       RUTH      EVELYN   
        11/08/2016 GENERAL     AABEL       RUTH      EVELYN   
        11/04/2014 GENERAL     AABEL       RUTH      EVELYN   
        11/06/2012 GENERAL     AABEL       RUTH      EVELYN   

                                             res_street_address res_city_desc  \
ncid    election_desc                                                           
AA56273 11/03/2020 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/06/2018 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/08/2016 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/04/2014 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   
        11/06/2012 GENERAL  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM   

                           state_cd  zip_code race_code ethnic_code party_cd  \
ncid    election_desc                                                          
AA56273 11/03/2020 GENERAL       NC   27253.0         W          NL      UNA   
        11/06/2018 GENERAL       NC   27253.0         W          NL      UNA   
        11/08/2016 GENERAL       NC   27253.0         W          NL      UNA   
        11/04/2014 GENERAL       NC   27253.0         W          NL     

In [30]:
## Create a dataframe indexed by ncid that records whether and how a person
  ## voted in each major election
voter_elecs_slice = voter_elecs_mi['vote_method_cat'].copy()
maj_elec_methods = voter_elecs_slice.unstack().drop(columns='None')

# Reorder columns
maj_elec_methods = maj_elec_methods[['11/03/2020 GENERAL',
                                     '11/06/2018 GENERAL',
                                     '11/08/2016 GENERAL',
                                     '11/04/2014 GENERAL',
                                     '11/06/2012 GENERAL']]
# Rename columns
maj_elec_methods.columns = ['Gen_2020', 
                            'Gen_2018', 
                            'Gen_2016',
                            'Gen_2014', 
                            'Gen_2012']

# Null values indicate the person did not cast a vote for the election, so
  # make 'No Vote' its own category
maj_elec_methods.fillna('No Vote', inplace=True)

# Inspect df
maj_elec_methods

Gen_2020      Gen_2018 Gen_2016      Gen_2014      Gen_2012
ncid                                                                     
AA100000         Early       No Vote    Early       No Vote       No Vote
AA100004       No Vote       No Vote  No Vote       No Vote       No Vote
AA100006         Early  Election Day    Early  Election Day         Early
AA100007         Early         Early    Early         Early         Early
AA100008       No Vote       No Vote  No Vote       No Vote  Election Day
...                ...           ...      ...           ...           ...
ES9989           Early  Election Day    Early         Early       No Vote
ES9991    Election Day       No Vote  No Vote  Election Day  Election Day
ES9992           Early         Early    Early         Early         Early
ES9997           Early         Early    Early         Early         Early
ES9999           Early         Early    Early         Early         Early

[7415235 rows x 5 columns]

In [31]:
## Check length of df prior to merging with maj_elec_methods
len(voter_elecs)

44491410

In [32]:
## Merge voter_elecs df with maj_elecs_methods according to ncid
voter_elecs = voter_elecs.merge(maj_elec_methods, how='left',
                                   on='ncid')
# Inspect updated df
print(len(voter_elecs)) # length did not change
voter_elecs.head()

44491410


ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0  AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1  AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2  AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3  AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4  AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   

  election_lbl  registr_in_time  birth_age_adj     voting_method  \
0   2020-11-03                1           85.0  ABSENTEE BY MAIL   
1   2018-11-06                1           83.0         IN-PERSON   
2   2016-11-08                1           81.0         IN-PERSON   
3   2014-11-04                1           79.0         IN-PERSON   
4   2012-11-06                1           77.0         IN-PERSON   

  vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0           Early            UNA       08N              1.0       08N   
1    Election Day            UNA       08N              1.0       08N   
2    Election Day            UNA       08N              1.0       08N   
3    Election Day            UNA       08N              1.0       08N   
4    Election Day            UNA       08N              1.0       08N   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
1            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
2            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
3            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
4            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   

                    res_street_address res_city_desc state_cd  zip_code  \
0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
1  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
2  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
3  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
4  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   

  race_code ethnic_code party_cd gender_code  birth_age birth_state  \
0         W          NL      UNA           F         85          NY   
1         W          NL      UNA           F         85          NY   
2         W          NL      UNA           F         85          NY   
3         W          NL      UNA           F         85          NY   
4         W          NL      UNA           F         85          NY   

  drivers_lic registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0           N 1984-10-01            08N             13.0               15A   
1           N 1984-10-01            08N             13.0               15A   
2           N 1984-10-01            08N             13.0               15A   
3           N 1984-10-01            08N             13.0               15A   
4           N 1984-10-01            08N             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv Gen_2020      Gen_2018  \
0          17.0                N        1935       08N    Early  Election Day   
1          17.0                N        1935       08N    Early  Election Day   
2          17.0                N        1935       08N    Early  Election Day   
3          17.0                N        1935       08N    Early  Election Day   
4          17.0                N        1

In [33]:
voter_elecs.head(35)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   
25   AA69747  11/06/2018 GENERAL            0        1.0      9019674.0   
26   AA69747  11/08/2016 GENERAL            0        1.0      9019674.0   
27   AA69747  11/04/2014 GENERAL            0        1.0      9019674.0   
28   AA69747  11/06/2012 GENERAL            0        1.0      9019674.0   
29   AA69747                None            0        NaN            NaN   
30  AA170513  11/03/2020 GENERAL            0        1.0      9129589.0   
31  AA170513  11/06/2018 GENERAL            0        1.0      9129589.0   
32  AA170513  11/08/2016 GENERAL            0        1.0      9129589.0   
33  AA170513  11/04/2014 GENERAL            0        1.0      9129589.0   
34  AA170513  11/06/2012 GENERAL            0        1.0      9129589.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN

In [34]:
# voter_elecs.to_csv('Data/NC_full_voter_elecs_final.zip', index=False)

In [35]:
voter_elecs.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 44491410 entries, 0 to 44491409
Data columns (total 47 columns):
 #   Column                    Non-Null Count     Dtype         
---  ------                    --------------     -----         
 0   ncid                      44491410 non-null  object        
 1   election_desc             44491410 non-null  object        
 2   no_vote_his               44491410 non-null  int64         
 3   county_id                 20092689 non-null  float64       
 4   voter_reg_num             20092689 non-null  float64       
 5   election_lbl              37076175 non-null  datetime64[ns]
 6   registr_in_time           44491410 non-null  int64         
 7   birth_age_adj             37076175 non-null  float64       
 8   voting_method             20092689 non-null  object        
 9   vote_method_cat           20092665 non-null  object        
 10  voted_party_cd            20084403 non-null  object        
 11  pct_label                 20092689 

In [5]:
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_final.zip',
                          dtype={'precinct_abbrv': str, 
                              'super_court_abbrv': str, 
                              'judic_dist_abbrv': str,
                              'school_dist_abbrv': str,
                              'vtd_abbrv': str
                                })

voter_elecs['election_lbl'] = pd.to_datetime(voter_elecs['election_lbl'])
voter_elecs.head()

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0  AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1  AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2  AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3  AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4  AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   

  election_lbl  registr_in_time  birth_age_adj     voting_method  \
0   2020-11-03                1           85.0  ABSENTEE BY MAIL   
1   2018-11-06                1           83.0         IN-PERSON   
2   2016-11-08                1           81.0         IN-PERSON   
3   2014-11-04                1           79.0         IN-PERSON   
4   2012-11-06                1           77.0         IN-PERSON   

  vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0           Early            UNA       08N              1.0       08N   
1    Election Day            UNA       08N              1.0       08N   
2    Election Day            UNA       08N              1.0       08N   
3    Election Day            UNA       08N              1.0       08N   
4    Election Day            UNA       08N              1.0       08N   

  voter_status_desc voter_status_reason_desc last_name first_name middle_name  \
0            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
1            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
2            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
3            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   
4            ACTIVE                 VERIFIED     AABEL       RUTH      EVELYN   

                    res_street_address res_city_desc state_cd  zip_code  \
0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
1  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
2  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
3  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   
4  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   27253.0   

  race_code ethnic_code party_cd gender_code  birth_age birth_state  \
0         W          NL      UNA           F         85          NY   
1         W          NL      UNA           F         85          NY   
2         W          NL      UNA           F         85          NY   
3         W          NL      UNA           F         85          NY   
4         W          NL      UNA           F         85          NY   

  drivers_lic  registr_dt precinct_abbrv  cong_dist_abbrv super_court_abbrv  \
0           N  1984-10-01            08N             13.0               15A   
1           N  1984-10-01            08N             13.0               15A   
2           N  1984-10-01            08N             13.0               15A   
3           N  1984-10-01            08N             13.0               15A   
4           N  1984-10-01            08N             13.0               15A   

  judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0              15A             24.0            64.0               NaN   
1              15A             24.0            64.0               NaN   
2              15A             24.0            64.0               NaN   
3              15A             24.0            64.0               NaN   
4              15A             24.0            64.0               NaN   

   dist_1_abbrv confidential_ind  birth_year vtd_abbrv Gen_2020      Gen_2018  \
0          17.0                N        1935       08N    Early  Election Day   
1          17.0                N        1935       08N    Early  Election Day   
2          17.0                N        1935       08N    Early  Election Day   
3          17.0                N        1935       08N    Early  Election Day   
4          17.0                N   

In [11]:
voter_elecs.head(35)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   
25   AA69747  11/06/2018 GENERAL            0        1.0      9019674.0   
26   AA69747  11/08/2016 GENERAL            0        1.0      9019674.0   
27   AA69747  11/04/2014 GENERAL            0        1.0      9019674.0   
28   AA69747  11/06/2012 GENERAL            0        1.0      9019674.0   
29   AA69747                None            0        NaN            NaN   
30  AA170513  11/03/2020 GENERAL            0        1.0      9129589.0   
31  AA170513  11/06/2018 GENERAL            0        1.0      9129589.0   
32  AA170513  11/08/2016 GENERAL            0        1.0      9129589.0   
33  AA170513  11/04/2014 GENERAL            0        1.0      9129589.0   
34  AA170513  11/06/2012 GENERAL            0        1.0      9129589.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN

In [12]:
## Create a df that summarizes the information known for each ncid
  ## (one record for each ncid)
ncid_summary = voter_elecs.copy()

# Reorder and only include certain columns
ncid_summary = ncid_summary[['ncid', 'no_vote_his', 'voter_status_desc',
                             'voter_status_reason_desc', 'last_name', 
                             'first_name', 'middle_name','party_cd', 
                             'gender_code', 'birth_age', 'birth_year',
                             'registr_dt', 'race_code','ethnic_code', 
                             'zip_code', 'res_street_address',
                             'res_city_desc', 'state_cd', 'birth_state', 
                             'drivers_lic', 'precinct_abbrv',
                             'vtd_abbrv', 'cong_dist_abbrv', 
                             'super_court_abbrv', 'judic_dist_abbrv', 
                             'nc_senate_abbrv', 'nc_house_abbrv', 
                             'school_dist_abbrv', 'Gen_2020', 'Gen_2018',
                             'Gen_2016', 'Gen_2014', 'Gen_2012'   
                            ]]
# With columns that make a record specific to a single election excluded,
  # each row corresponding to a unique ncid should be identical to the others. 
  # Thus, only one row per unique ncid is needed now, drop duplicates
ncid_summary.drop_duplicates(inplace=True)

# Inspect new df
ncid_summary.head()

ncid  no_vote_his voter_status_desc voter_status_reason_desc  \
0    AA56273            0            ACTIVE                 VERIFIED   
6   AA201627            0            ACTIVE                 VERIFIED   
12  AA216996            0            ACTIVE     VERIFICATION PENDING   
18   AA98377            0            ACTIVE                 VERIFIED   
24   AA69747            0            ACTIVE                 VERIFIED   

     last_name first_name middle_name party_cd gender_code  birth_age  \
0        AABEL       RUTH      EVELYN      UNA           F         85   
6       AARDEN       JONI      AUTUMN      UNA           F         42   
12  AARMSTRONG    TIMOTHY       DUANE      REP           M         54   
18       AARON  CHRISTINA    CASTAGNA      UNA           F         44   
24       AARON    CLAUDIA      HAYDEN      UNA           F         75   

    birth_year  registr_dt race_code ethnic_code  zip_code  \
0         1935  1984-10-01         W          NL   27253.0   
6         1978  2018-02-23         W          UN   27302.0   
12        1966  2020-10-31         W          UN   27302.0   
18        1976  1996-03-26         W          UN   27215.0   
24        1945  1989-08-15         W          NL   27215.0   

                     res_street_address res_city_desc state_cd birth_state  \
0   4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC          NY   
6                      117 W CLAY ST           MEBANE       NC          DC   
12               3670  COVINGTON TRL           MEBANE       NC          AL   
18                    421  WHITT AVE       BURLINGTON       NC          NC   
24                    1013  EDITH ST       BURLINGTON       NC          VA   

   drivers_lic precinct_abbrv vtd_abbrv  cong_dist_abbrv super_court_abbrv  \
0            N            08N       08N             13.0               15A   
6            Y            10N       10N             13.0               15A   
12           N            103       103             13.0               15A   
18           Y            03S       03S             13.0               15A   
24           Y            124       124             13.0               15A   

   judic_dist_abbrv  nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  \
0               15A             24.0            64.0               NaN   
6               15A             24.0            63.0               NaN   
12              15A             24.0            63.0               NaN   
18              15A             24.0            64.0               NaN   
24              15A             24.0            63.0               NaN   

   Gen_2020      Gen_2018      Gen_2016      Gen_2014      Gen_2012  
0     Early  Election Day  Election Day  Election Day  Election Day  
6     Early       No Vote       No Vote       No Vote       No Vote  
12    Early       No Vote       No Vote       No Vote       No Vote  
18    Early  Election Day         Early         Early         Early  
24    Early         Early         Early  Election Day         Early

In [13]:
## Check length of new df and number of unique ncid's to ensure each 
  ## appears only once
print(len(ncid_summary))
ncid_summary['ncid'].nunique()

7415235


7415235

In [8]:
## Check metadata for new summary df
ncid_summary.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14463167 entries, 0 to 44491404
Data columns (total 35 columns):
 #   Column                    Non-Null Count     Dtype  
---  ------                    --------------     -----  
 0   ncid                      14463167 non-null  object 
 1   no_vote_his               14463167 non-null  int64  
 2   voter_status_desc         14463167 non-null  object 
 3   voter_status_reason_desc  14463165 non-null  object 
 4   last_name                 14462847 non-null  object 
 5   first_name                14462980 non-null  object 
 6   middle_name               13481941 non-null  object 
 7   party_cd                  14463167 non-null  object 
 8   gender_code               14463167 non-null  object 
 9   birth_age                 14463167 non-null  int64  
 10  birth_year                14463167 non-null  int64  
 11  registr_dt                14463167 non-null  object 
 12  race_code                 14463167 non-null  object 
 13  ethnic_cod

In [40]:
# ncid_summary.to_csv('Data/NC_ncid_summary.zip', index=False)

## Create Separate DataFrames for Each Election

In [4]:
voter_elecs = pd.read_csv('Data/NC_full_voter_elecs_final.zip',
                          dtype={'precinct_abbrv': str, 
                              'super_court_abbrv': str, 
                              'judic_dist_abbrv': str,
                              'school_dist_abbrv': str,
                              'vtd_abbrv': str
                                })

voter_elecs['election_lbl'] = pd.to_datetime(voter_elecs['election_lbl'])

In [5]:
voter_elecs.head(25)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
0    AA56273  11/03/2020 GENERAL            0        1.0      9005990.0   
1    AA56273  11/06/2018 GENERAL            0        1.0      9005990.0   
2    AA56273  11/08/2016 GENERAL            0        1.0      9005990.0   
3    AA56273  11/04/2014 GENERAL            0        1.0      9005990.0   
4    AA56273  11/06/2012 GENERAL            0        1.0      9005990.0   
5    AA56273                None            0        NaN            NaN   
6   AA201627  11/03/2020 GENERAL            0        1.0      9178574.0   
7   AA201627  11/06/2018 GENERAL            0        NaN            NaN   
8   AA201627  11/08/2016 GENERAL            0        NaN            NaN   
9   AA201627  11/04/2014 GENERAL            0        NaN            NaN   
10  AA201627  11/06/2012 GENERAL            0        NaN            NaN   
11  AA201627                None            0        NaN            NaN   
12  AA216996  11/03/2020 GENERAL            0        1.0      9205561.0   
13  AA216996  11/06/2018 GENERAL            0        NaN            NaN   
14  AA216996  11/08/2016 GENERAL            0        NaN            NaN   
15  AA216996  11/04/2014 GENERAL            0        NaN            NaN   
16  AA216996  11/06/2012 GENERAL            0        NaN            NaN   
17  AA216996                None            0        NaN            NaN   
18   AA98377  11/03/2020 GENERAL            0        1.0      9048723.0   
19   AA98377  11/06/2018 GENERAL            0        1.0      9048723.0   
20   AA98377  11/08/2016 GENERAL            0        1.0      9048723.0   
21   AA98377  11/04/2014 GENERAL            0        1.0      9048723.0   
22   AA98377  11/06/2012 GENERAL            0        1.0      9048723.0   
23   AA98377                None            0        NaN            NaN   
24   AA69747  11/03/2020 GENERAL            0        1.0      9019674.0   

   election_lbl  registr_in_time  birth_age_adj     voting_method  \
0    2020-11-03                1           85.0  ABSENTEE BY MAIL   
1    2018-11-06                1           83.0         IN-PERSON   
2    2016-11-08                1           81.0         IN-PERSON   
3    2014-11-04                1           79.0         IN-PERSON   
4    2012-11-06                1           77.0         IN-PERSON   
5           NaT                1            NaN               NaN   
6    2020-11-03                1           42.0  ABSENTEE ONESTOP   
7    2018-11-06                1           40.0               NaN   
8    2016-11-08                0           38.0               NaN   
9    2014-11-04                0           36.0               NaN   
10   2012-11-06                0           34.0               NaN   
11          NaT                1            NaN               NaN   
12   2020-11-03                1           54.0  ABSENTEE ONESTOP   
13   2018-11-06                0           52.0               NaN   
14   2016-11-08                0           50.0               NaN   
15   2014-11-04                0           48.0               NaN   
16   2012-11-06                0           46.0               NaN   
17          NaT                1            NaN               NaN   
18   2020-11-03                1           44.0  ABSENTEE ONESTOP   
19   2018-11-06                1           42.0         IN-PERSON   
20   2016-11-08                1           40.0  ABSENTEE ONESTOP   
21   2014-11-04                1           38.0  ABSENTEE ONESTOP   
22   2012-11-06                1           36.0  ABSENTEE ONESTOP   
23          NaT                1            NaN               NaN   
24   2020-11-03                1           75.0  ABSENTEE ONESTOP   

   vote_method_cat voted_party_cd pct_label  voted_county_id vtd_label  \
0            Early            UNA       08N              1.0       08N   
1     Election Day            UNA       08N              1.0       08N   
2     Election Day            UNA       

In [6]:
## Define function to automate assembling election specific dataframes
def get_election_df(yr):
    
    # Copy original df
    df = voter_elecs.copy()

    # Filter to get only the rows specific to the desired election
    df = df.loc[df['election_lbl'].dt.year==yr]

    # Only keep those voters who registered in time
    df = df.loc[df['registr_in_time']==1]
    
    # Only keep those voters who were old enough to vote in the election
      # (apparently some registration date info is incorrect)
    df = df.loc[df['birth_age_adj']>=18]

    # Reorder and drop certain columns
    df = df[['ncid', 'no_vote_his', 'birth_age_adj', 'voting_method', 
             'Gen_{}'.format(yr), 'party_cd', 'gender_code', 'birth_year', 
             'registr_dt', 'race_code', 'ethnic_code', 'zip_code', 
             'res_street_address', 'res_city_desc', 'state_cd', 'birth_state',
             'drivers_lic', 'county_id', 'voted_county_id', 'precinct_abbrv',
             'vtd_abbrv', 'cong_dist_abbrv', 'super_court_abbrv', 
             'judic_dist_abbrv', 'nc_senate_abbrv', 'nc_house_abbrv',
             'school_dist_abbrv'
            ]]
    
    return df

### General 2020

In [17]:
## Make dataframe specific to 2020 general election
gen_2020 = get_election_df(2020)
print(len(gen_2020))
display(gen_2020.head())
gen_2020.tail()

7347946


ncid  no_vote_his  birth_age_adj     voting_method Gen_2020 party_cd  \
0    AA56273            0           85.0  ABSENTEE BY MAIL    Early      UNA   
6   AA201627            0           42.0  ABSENTEE ONESTOP    Early      UNA   
12  AA216996            0           54.0  ABSENTEE ONESTOP    Early      REP   
18   AA98377            0           44.0  ABSENTEE ONESTOP    Early      UNA   
24   AA69747            0           75.0  ABSENTEE ONESTOP    Early      UNA   

   gender_code  birth_year  registr_dt race_code ethnic_code  zip_code  \
0            F        1935  1984-10-01         W          NL   27253.0   
6            F        1978  2018-02-23         W          UN   27302.0   
12           M        1966  2020-10-31         W          UN   27302.0   
18           F        1976  1996-03-26         W          UN   27215.0   
24           F        1945  1989-08-15         W          NL   27215.0   

                     res_street_address res_city_desc state_cd birth_state  \
0   4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC          NY   
6                      117 W CLAY ST           MEBANE       NC          DC   
12               3670  COVINGTON TRL           MEBANE       NC          AL   
18                    421  WHITT AVE       BURLINGTON       NC          NC   
24                    1013  EDITH ST       BURLINGTON       NC          VA   

   drivers_lic  county_id  voted_county_id precinct_abbrv vtd_abbrv  \
0            N        1.0              1.0            08N       08N   
6            Y        1.0              1.0            10N       10N   
12           N        1.0              1.0            103       103   
18           Y        1.0              1.0            03S       03S   
24           Y        1.0              1.0            124       124   

    cong_dist_abbrv super_court_abbrv judic_dist_abbrv  nc_senate_abbrv  \
0              13.0               15A              15A             24.0   
6              13.0               15A              15A             24.0   
12             13.0               15A              15A             24.0   
18             13.0               15A              15A             24.0   
24             13.0               15A              15A             24.0   

    nc_house_abbrv school_dist_abbrv  
0             64.0               NaN  
6             63.0               NaN  
12            63.0               NaN  
18            64.0               NaN  
24            63.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method Gen_2020  \
44491380  ES17204            0           54.0  ABSENTEE ONESTOP    Early   
44491386  ES26341            0           57.0  ABSENTEE ONESTOP    Early   
44491392  ES26380            0           65.0  ABSENTEE BY MAIL    Early   
44491398  ES28936            1           36.0               NaN  No Vote   
44491404  ES27200            1           56.0               NaN  No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491380      UNA           F        1966  2000-06-01         W          NL   
44491386      REP           F        1963  2015-11-30         W          NL   
44491392      UNA           F        1955  2015-12-18         W          NL   
44491398      UNA           U        1984  2020-06-09         U          UN   
44491404      REP           F        1964  2016-12-29         W          NL   

          zip_code            res_street_address   res_city_desc state_cd  \
44491380   28714.0       2156  LICKSKILLET RD         BURNSVILLE       NC   
44491386   28714.0       250  LAUREL ACRES RD         BURNSVILLE       NC   
44491392   28714.0  91 W BURNSVILLE CHURCH RD         BURNSVILLE       NC   
44491398   28740.0            225  GARLAND LN     GREEN MOUNTAIN       NC   
44491404   28714.0  115  STONEY FALLS LOOP   #D3      BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491380          FL           Y      100.0            100.0         02 CAN   
44491386          CO           Y      100.0            100.0         08 CRA   
44491392          NC           Y      100.0            100.0         01 BUR   
44491398         NaN           Y        NaN              NaN         05 GRE   
44491404          IN           Y        NaN              NaN         11 PRI   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491380    02-CAN             11.0                24               24   
44491386    08-CRA             11.0                24               24   
44491392    01-BUR             11.0                24               24   
44491398    05-GRE             11.0                24               24   
44491404    11-PRI             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491380             47.0           118.0               NaN  
44491386             47.0           118.0               NaN  
44491392             47.0           118.0               NaN  
44491398             47.0           118.0               NaN  
44491404             47.0           118.0               NaN

In [18]:
# gen_2020.to_csv('Data/NC_gen_2020.zip', index=False)

### General 2018

In [19]:
## Make dataframe specific to 2018 general election
gen_2018 = get_election_df(2018)
print(len(gen_2018))
display(gen_2018.head())
gen_2018.tail()

6050078


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2018  \
1    AA56273            0           83.0         IN-PERSON  Election Day   
7   AA201627            0           40.0               NaN       No Vote   
19   AA98377            0           42.0         IN-PERSON  Election Day   
25   AA69747            0           73.0  ABSENTEE ONESTOP         Early   
31  AA170513            0           70.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
1       UNA           F        1935  1984-10-01         W          NL   
7       UNA           F        1978  2018-02-23         W          UN   
19      UNA           F        1976  1996-03-26         W          UN   
25      UNA           F        1945  1989-08-15         W          NL   
31      DEM           M        1948  2012-03-07         W          UN   

    zip_code                   res_street_address res_city_desc state_cd  \
1    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
7    27302.0                     117 W CLAY ST           MEBANE       NC   
19   27215.0                    421  WHITT AVE       BURLINGTON       NC   
25   27215.0                    1013  EDITH ST       BURLINGTON       NC   
31   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
1           NY           N        1.0              1.0            08N   
7           DC           Y        NaN              NaN            10N   
19          NC           Y        1.0              1.0            03S   
25          VA           Y        1.0              1.0            124   
31          MA           N        1.0              1.0            08N   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
1        08N             13.0               15A              15A   
7        10N             13.0               15A              15A   
19       03S             13.0               15A              15A   
25       124             13.0               15A              15A   
31       08N             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
1              24.0            64.0               NaN  
7              24.0            63.0               NaN  
19             24.0            64.0               NaN  
25             24.0            63.0               NaN  
31             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method Gen_2018  \
44491375  ES26387            0           20.0  ABSENTEE BY MAIL    Early   
44491381  ES17204            0           52.0  ABSENTEE ONESTOP    Early   
44491387  ES26341            0           55.0  ABSENTEE ONESTOP    Early   
44491393  ES26380            0           63.0               NaN  No Vote   
44491405  ES27200            1           54.0               NaN  No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491375      UNA           F        1998  2015-12-31         W          NL   
44491381      UNA           F        1966  2000-06-01         W          NL   
44491387      REP           F        1963  2015-11-30         W          NL   
44491393      UNA           F        1955  2015-12-18         W          NL   
44491405      REP           F        1964  2016-12-29         W          NL   

          zip_code            res_street_address res_city_desc state_cd  \
44491375   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491381   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491387   28714.0       250  LAUREL ACRES RD       BURNSVILLE       NC   
44491393   28714.0  91 W BURNSVILLE CHURCH RD       BURNSVILLE       NC   
44491405   28714.0  115  STONEY FALLS LOOP   #D3    BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491375          NC           Y      100.0            100.0         02 CAN   
44491381          FL           Y      100.0            100.0         02 CAN   
44491387          CO           Y      100.0            100.0         08 CRA   
44491393          NC           Y        NaN              NaN         01 BUR   
44491405          IN           Y        NaN              NaN         11 PRI   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491375    02-CAN             11.0                24               24   
44491381    02-CAN             11.0                24               24   
44491387    08-CRA             11.0                24               24   
44491393    01-BUR             11.0                24               24   
44491405    11-PRI             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491375             47.0           118.0               NaN  
44491381             47.0           118.0               NaN  
44491387             47.0           118.0               NaN  
44491393             47.0           118.0               NaN  
44491405             47.0           118.0               NaN

In [20]:
# gen_2018.to_csv('Data/NC_gen_2018.zip', index=False)

### General 2016

In [21]:
## Make dataframe specific to 2016 general election
gen_2016 = get_election_df(2016)
print(len(gen_2016))
display(gen_2016.head())
gen_2016.tail()

5516340


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2016  \
2    AA56273            0           81.0         IN-PERSON  Election Day   
20   AA98377            0           40.0  ABSENTEE ONESTOP         Early   
26   AA69747            0           71.0  ABSENTEE ONESTOP         Early   
32  AA170513            0           68.0  ABSENTEE ONESTOP         Early   
38   BM49306            0           50.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
2       UNA           F        1935  1984-10-01         W          NL   
20      UNA           F        1976  1996-03-26         W          UN   
26      UNA           F        1945  1989-08-15         W          NL   
32      DEM           M        1948  2012-03-07         W          UN   
38      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
2    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
20   27215.0                    421  WHITT AVE       BURLINGTON       NC   
26   27215.0                    1013  EDITH ST       BURLINGTON       NC   
32   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
38   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
2           NY           N        1.0              1.0            08N   
20          NC           Y        1.0              1.0            03S   
26          VA           Y        1.0              1.0            124   
32          MA           N        1.0              1.0            08N   
38          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
2        08N             13.0               15A              15A   
20       03S             13.0               15A              15A   
26       124             13.0               15A              15A   
32       08N             13.0               15A              15A   
38       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
2              24.0            64.0               NaN  
20             24.0            64.0               NaN  
26             24.0            63.0               NaN  
32             24.0            64.0               NaN  
38             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2016  \
44491370  ES26136            0           19.0  ABSENTEE BY MAIL         Early   
44491376  ES26387            0           18.0  ABSENTEE BY MAIL         Early   
44491382  ES17204            0           50.0  ABSENTEE ONESTOP         Early   
44491388  ES26341            0           53.0         IN-PERSON  Election Day   
44491394  ES26380            0           61.0               NaN       No Vote   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491370      UNA           F        1997  2016-08-02         W          NL   
44491376      UNA           F        1998  2015-12-31         W          NL   
44491382      UNA           F        1966  2000-06-01         W          NL   
44491388      REP           F        1963  2015-11-30         W          NL   
44491394      UNA           F        1955  2015-12-18         W          NL   

          zip_code            res_street_address res_city_desc state_cd  \
44491370   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491376   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491382   28714.0       2156  LICKSKILLET RD       BURNSVILLE       NC   
44491388   28714.0       250  LAUREL ACRES RD       BURNSVILLE       NC   
44491394   28714.0  91 W BURNSVILLE CHURCH RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491370          NC           Y      100.0            100.0         02 CAN   
44491376          NC           Y      100.0            100.0         02 CAN   
44491382          FL           Y      100.0            100.0         02 CAN   
44491388          CO           Y      100.0            100.0         08 CRA   
44491394          NC           Y        NaN              NaN         01 BUR   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491370    02-CAN             11.0                24               24   
44491376    02-CAN             11.0                24               24   
44491382    02-CAN             11.0                24               24   
44491388    08-CRA             11.0                24               24   
44491394    01-BUR             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491370             47.0           118.0               NaN  
44491376             47.0           118.0               NaN  
44491382             47.0           118.0               NaN  
44491388             47.0           118.0               NaN  
44491394             47.0           118.0               NaN

In [22]:
# gen_2016.to_csv('Data/NC_gen_2016.zip', index=False)

### General 2014

In [23]:
## Make dataframe specific to 2014 general election
gen_2014 = get_election_df(2014)
print(len(gen_2014))
display(gen_2014.head())
gen_2014.tail()

4486408


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2014  \
3    AA56273            0           79.0         IN-PERSON  Election Day   
21   AA98377            0           38.0  ABSENTEE ONESTOP         Early   
27   AA69747            0           69.0         IN-PERSON  Election Day   
33  AA170513            0           66.0  ABSENTEE BY MAIL         Early   
39   BM49306            0           48.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
3       UNA           F        1935  1984-10-01         W          NL   
21      UNA           F        1976  1996-03-26         W          UN   
27      UNA           F        1945  1989-08-15         W          NL   
33      DEM           M        1948  2012-03-07         W          UN   
39      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
3    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
21   27215.0                    421  WHITT AVE       BURLINGTON       NC   
27   27215.0                    1013  EDITH ST       BURLINGTON       NC   
33   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
39   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
3           NY           N        1.0              1.0            08N   
21          NC           Y        1.0              1.0            03S   
27          VA           Y        1.0              1.0            124   
33          MA           N        1.0              1.0            08N   
39          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
3        08N             13.0               15A              15A   
21       03S             13.0               15A              15A   
27       124             13.0               15A              15A   
33       08N             13.0               15A              15A   
39       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
3              24.0            64.0               NaN  
21             24.0            64.0               NaN  
27             24.0            63.0               NaN  
33             24.0            64.0               NaN  
39             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2014  \
44491329  ES25745            0           58.0         IN-PERSON  Election Day   
44491335  ES25768            0           60.0               NaN       No Vote   
44491341  ES20237            0           62.0               NaN       No Vote   
44491365  ES17216            0           62.0  ABSENTEE ONESTOP         Early   
44491383  ES17204            0           48.0         IN-PERSON  Election Day   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491329      UNA           M        1956  2014-07-11         W          NL   
44491335      UNA           F        1954  2014-08-07         W          NL   
44491341      REP           M        1952  2004-09-27         W          UN   
44491365      UNA           M        1952  2000-06-15         W          NL   
44491383      UNA           F        1966  2000-06-01         W          NL   

          zip_code       res_street_address res_city_desc state_cd  \
44491329   28714.0        202  HAMLET DR       BURNSVILLE       NC   
44491335   28714.0        202  HAMLET DR       BURNSVILLE       NC   
44491341   28714.0          178  WREN DR       BURNSVILLE       NC   
44491365   28714.0  2156  LICKSKILLET RD       BURNSVILLE       NC   
44491383   28714.0  2156  LICKSKILLET RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491329          PA           Y      100.0            100.0         02 CAN   
44491335          IL           Y        NaN              NaN         02 CAN   
44491341          IL           N        NaN              NaN         01 BUR   
44491365          MI           Y      100.0            100.0         02 CAN   
44491383          FL           Y      100.0            100.0         02 CAN   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491329    02-CAN             11.0                24               24   
44491335    02-CAN             11.0                24               24   
44491341    01-BUR             11.0                24               24   
44491365    02-CAN             11.0                24               24   
44491383    02-CAN             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491329             47.0           118.0               NaN  
44491335             47.0           118.0               NaN  
44491341             47.0           118.0               NaN  
44491365             47.0           118.0               NaN  
44491383             47.0           118.0               NaN

In [24]:
# gen_2014.to_csv('Data/NC_gen_2014.zip', index=False)

### General 2012

In [7]:
## Make dataframe specific to 2012 general election
gen_2012 = get_election_df(2012)
print(len(gen_2012))
display(gen_2012.head())
gen_2012.tail()

4386614


ncid  no_vote_his  birth_age_adj     voting_method      Gen_2012  \
4    AA56273            0           77.0         IN-PERSON  Election Day   
22   AA98377            0           36.0  ABSENTEE ONESTOP         Early   
28   AA69747            0           67.0  ABSENTEE ONESTOP         Early   
34  AA170513            0           64.0  ABSENTEE ONESTOP         Early   
40   BM49306            0           46.0  ABSENTEE ONESTOP         Early   

   party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
4       UNA           F        1935  1984-10-01         W          NL   
22      UNA           F        1976  1996-03-26         W          UN   
28      UNA           F        1945  1989-08-15         W          NL   
34      DEM           M        1948  2012-03-07         W          UN   
40      DEM           F        1966  2020-06-01         B          NL   

    zip_code                   res_street_address res_city_desc state_cd  \
4    27253.0  4430 E GREENSBORO-CHAPEL HILL RD           GRAHAM       NC   
22   27215.0                    421  WHITT AVE       BURLINGTON       NC   
28   27215.0                    1013  EDITH ST       BURLINGTON       NC   
34   27253.0             5608  OLD CHEROKEE LN           GRAHAM       NC   
40   27215.0             187  CAVALIER WAY   #104    BURLINGTON       NC   

   birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
4           NY           N        1.0              1.0            08N   
22          NC           Y        1.0              1.0            03S   
28          VA           Y        1.0              1.0            124   
34          MA           N        1.0              1.0            08N   
40          NC           Y        1.0              7.0            03S   

   vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
4        08N             13.0               15A              15A   
22       03S             13.0               15A              15A   
28       124             13.0               15A              15A   
34       08N             13.0               15A              15A   
40       03S             13.0               15A              15A   

    nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
4              24.0            64.0               NaN  
22             24.0            64.0               NaN  
28             24.0            63.0               NaN  
34             24.0            64.0               NaN  
40             24.0            64.0               NaN

ncid  no_vote_his  birth_age_adj     voting_method      Gen_2012  \
44491318  ES15279            0           51.0               NaN       No Vote   
44491324  ES13347            0           72.0         IN-PERSON  Election Day   
44491342  ES20237            0           60.0  ABSENTEE BY MAIL         Early   
44491366  ES17216            0           60.0  ABSENTEE ONESTOP         Early   
44491384  ES17204            0           46.0  ABSENTEE ONESTOP         Early   

         party_cd gender_code  birth_year  registr_dt race_code ethnic_code  \
44491318      REP           M        1961  1996-10-11         W          NL   
44491324      DEM           F        1940  1990-09-28         W          NL   
44491342      REP           M        1952  2004-09-27         W          UN   
44491366      UNA           M        1952  2000-06-15         W          NL   
44491384      UNA           F        1966  2000-06-01         W          NL   

          zip_code        res_street_address res_city_desc state_cd  \
44491318   28714.0  508  HANNAH BRANCH RD       BURNSVILLE       NC   
44491324   28714.0  565  SHUFORD CREEK RD       BURNSVILLE       NC   
44491342   28714.0           178  WREN DR       BURNSVILLE       NC   
44491366   28714.0   2156  LICKSKILLET RD       BURNSVILLE       NC   
44491384   28714.0   2156  LICKSKILLET RD       BURNSVILLE       NC   

         birth_state drivers_lic  county_id  voted_county_id precinct_abbrv  \
44491318          NY           Y        NaN              NaN         09 SOU   
44491324          CA           N      100.0            100.0         09 SOU   
44491342          IL           N      100.0            100.0         01 BUR   
44491366          MI           Y      100.0            100.0         02 CAN   
44491384          FL           Y      100.0            100.0         02 CAN   

         vtd_abbrv  cong_dist_abbrv super_court_abbrv judic_dist_abbrv  \
44491318    09-SOU             11.0                24               24   
44491324    09-SOU             11.0                24               24   
44491342    01-BUR             11.0                24               24   
44491366    02-CAN             11.0                24               24   
44491384    02-CAN             11.0                24               24   

          nc_senate_abbrv  nc_house_abbrv school_dist_abbrv  
44491318             47.0           118.0               NaN  
44491324             47.0           118.0               NaN  
44491342             47.0           118.0               NaN  
44491366             47.0           118.0               NaN  
44491384             47.0           118.0               NaN

In [8]:
# gen_2012.to_csv('Data/NC_gen_2012.zip', index=False)

In [11]:
OC_birth = voter_elecs.loc[voter_elecs['birth_state']=='OC']
OC_birth.loc[OC_birth['election_desc']=='11/03/2020 GENERAL'].head(100)

ncid       election_desc  no_vote_his  county_id  voter_reg_num  \
108    DE236758  11/03/2020 GENERAL            1        NaN            NaN   
318    AA196723  11/03/2020 GENERAL            0        1.0      9169910.0   
342    AA148060  11/03/2020 GENERAL            0        1.0      9099437.0   
360    DL221658  11/03/2020 GENERAL            0        1.0      9192802.0   
366    AA202162  11/03/2020 GENERAL            0        1.0      9179739.0   
630    AA207681  11/03/2020 GENERAL            0        1.0      9189263.0   
846    AA201921  11/03/2020 GENERAL            0        NaN            NaN   
870    AA206220  11/03/2020 GENERAL            1        NaN            NaN   
918    AA196880  11/03/2020 GENERAL            0        1.0      9170173.0   
924    AA187630  11/03/2020 GENERAL            0        1.0      9154729.0   
948    AA168552  11/03/2020 GENERAL            0        NaN            NaN   
1020   AA181290  11/03/2020 GENERAL            0        1.0      9144279.0   
1662   EH964773  11/03/2020 GENERAL            0        1.0      9185339.0   
1782   AA180310  11/03/2020 GENERAL            0        NaN            NaN   
2154   AA120416  11/03/2020 GENERAL            0        1.0      9071173.0   
2160   AA200216  11/03/2020 GENERAL            0        1.0      9175808.0   
2298   AA196432  11/03/2020 GENERAL            1        NaN            NaN   
2316   BY569147  11/03/2020 GENERAL            0        1.0      9172397.0   
2496   AA142045  11/03/2020 GENERAL            0        1.0      9157792.0   
2988    AA90680  11/03/2020 GENERAL            0        1.0      9040871.0   
3036   AA188362  11/03/2020 GENERAL            1        NaN            NaN   
3042   AA183113  11/03/2020 GENERAL            0        NaN            NaN   
3048   AA168800  11/03/2020 GENERAL            0        1.0      9127070.0   
3144   AA182516  11/03/2020 GENERAL            0        NaN            NaN   
3180   AA188487  11/03/2020 GENERAL            0        1.0      9156262.0   
3186   AA168612  11/03/2020 GENERAL            1        NaN            NaN   
3210   AA191695  11/03/2020 GENERAL            0        NaN            NaN   
3216   AA167091  11/03/2020 GENERAL            0        1.0      9124590.0   
3234   AA149513  11/03/2020 GENERAL            0        1.0      9101416.0   
3252   AA150483  11/03/2020 GENERAL            0        NaN            NaN   
3294   AA202374  11/03/2020 GENERAL            0        1.0      9180181.0   
3366   AA158846  11/03/2020 GENERAL            0        1.0      9113671.0   
3372   AA161166  11/03/2020 GENERAL            0        1.0      9116493.0   
3408   AA208392  11/03/2020 GENERAL            0        1.0      9190261.0   
3414   AA208393  11/03/2020 GENERAL            0        1.0      9190262.0   
3444   DE147689  11/03/2020 GENERAL            0        1.0      9184552.0   
3546   BL340584  11/03/2020 GENERAL            0        1.0      9169821.0   
3564   AA164353  11/03/2020 GENERAL            0        1.0      9120625.0   
3570   AA200349  11/03/2020 GENERAL            0        1.0      9176068.0   
3594   AA216451  11/03/2020 GENERAL            0        1.0      9204580.0   
3600   AA207626  11/03/2020 GENERAL            0        1.0      9189148.0   
3702   AA205973  11/03/2020 GENERAL            1        NaN            NaN   
3726    AA95042  11/03/2020 GENERAL            0        1.0      9045315.0   
3732   AA102074  11/03/2020 GENERAL            0        1.0      9052513.0   
3798   AA200846  11/03/2020 GENERAL            0        1.0      9177012.0   
3816   AA202125  11/03/2020 GENERAL            0        1.0      9179647.0   
3828   AA203250  11/03/2020 GENERAL            0        1.0      9181750.0   
3858   DE285754  11/03/2020 GENERAL            0        1.0      9203567.0   
3900   AA187217  11/03/2020 GENERAL            0        1.0      9154084.0   
3912   AA217000  11/03/2020 GENERAL            0        1.0      9205566.0   
3960   AA155809  11/03/2020 GENER